## Capstone Project The Battle of the Neighborhoods


## 1. Introduction: Business Problem 

This project is aimed at finding the optimal location to set a **Italian Reastaurant** in London,UK.

There are already many restaurants in London,we need to detect the **locations that did not already have restaurants**. Of course, not having too many **similar Italian restaurant is also important**.

Third, **the location should be as close to city center** as possible

## 2. Data

As what we intrduced before, there are four main factors to determine the location of the restaurant

1. number of restaurants existing in the neighborhoods

2. number of similar Italian restaurants in the neighborhoods

3. distance of neighborhoods from city center 

## Here are the data sources needed to acquire the required information

1. the coordinate of the city centre can be acquired by using **geopy library**

2. number of restaurants and their type and other type of buildings can be obtained by **Foursquare API**

3. The neiborhoods data can also be acquired by Foursquare API

#### Use geopy library to get the latitude and longitude values of Beijing.

In [1]:
import numpy as np 
import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json 
from geopy.geocoders import Nominatim 
import requests # library to handle requests
from pandas.io.json import json_normalize 
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium # map rendering library

In [2]:
address = 'London, UK'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of London are 51.5073219, -0.1276474.


In [3]:
#!pip install shapely
import shapely

#!pip install pyproj
import pyproj

import math
def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('London center longitude={}, latitude={}'.format(longitude,latitude))
x, y = lonlat_to_xy(longitude,latitude )
print('London center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('London center longitude={}, latitude={}'.format(lo, la))


Coordinate transformation check
-------------------------------
London center longitude=-0.1276474, latitude=51.5073219
London center UTM X=-547012.468459844, Y=5815556.876143048
London center longitude=-0.12764739999999858, latitude=51.5073219


C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


In [4]:
London_center_x, London_center_y = lonlat_to_xy(longitude,latitude) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = London_center_x - 6000
x_step = 600
y_min =London_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(London_center_x, London_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)



C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This 

In [21]:
map_London= folium.Map(location=[latitude,longitude], zoom_start=13)
folium.Marker(location=[latitude,longitude], popup='London').add_to(map_London)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_berlin) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_London)
    #folium.Marker([lat, lon]).add_to(map_berlin)
map_London

### Use geolocator to get the neighborhoods

In [6]:
CLIENT_ID = 'FCO1UB1PJBWY1Z1OX0EVQU0BU0EWOD4T5DQW55BWJLMLJ4QL' # your Foursquare ID
CLIENT_SECRET = 'KCWZFCZEG0NL1FPBT3WPW5ZCETAY0L03QIZYW21VQPRTSETV'
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)


Your credentails:
CLIENT_ID: FCO1UB1PJBWY1Z1OX0EVQU0BU0EWOD4T5DQW55BWJLMLJ4QL
CLIENT_SECRET:KCWZFCZEG0NL1FPBT3WPW5ZCETAY0L03QIZYW21VQPRTSETV


In [7]:
def get_address(latitude, longitude):
    location=geolocator.reverse([latitude, longitude])
    return location.address
addr = get_address(latitude, longitude)
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(latitude, longitude, addr))

Reverse geocoding check
-----------------------
Address of [51.5073219, -0.1276474] is: Westminster, Covent Garden, City of Westminster, London, Greater London, England, United Kingdom


In [9]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', United Kingdom', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [10]:
addresses[150:170]

['45, Waterman Way, St. George in the East, Wapping, London Borough of Tower Hamlets, London, Greater London, England, E1W 2QN',
 'Shadwell Basin, Glamis Road, Ratcliffe, Wapping, London Borough of Tower Hamlets, London, Greater London, England, E1W 3TF',
 'Ratcliffe, Stepney, London Borough of Tower Hamlets, London, Greater London, England',
 "Shaftesbury Place, 135, Warwick Road, Earl's Court, Royal Borough of Kensington and Chelsea, London, Greater London, England, W14 8NJ",
 "Redfield Lane, Earl's Court, Royal Borough of Kensington and Chelsea, London, Greater London, England, SW5 0RG",
 'Foundation House, 114, Cromwell Road, South Kensington, Royal Borough of Kensington and Chelsea, London, Greater London, England, SW7 4ER',
 'Natural History Museum, Cromwell Road, Brompton, Royal Borough of Kensington and Chelsea, London, Greater London, England, SW7 5BD',
 'Paul Edmonds, Brompton Road, Royal Borough of Kensington and Chelsea, London, Greater London, England, SW3 2EJ',
 'Giuseppe

In [11]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0  Elms Crescent, Abbeville Village, Clapham Park...  51.454405  -0.135857   
1  Londis, 17-20, Prague Place, Abbeville Village...  51.455507  -0.127522   
2  Trinity Academy, 56, Brixton Hill, Stockwell, ...  51.456608  -0.119185   
3  Jelf Road, Herne Hill, London Borough of Lambe...  51.457708  -0.110849   
4  Milkwood Road, West Dulwich, Herne Hill, Londo...  51.458808  -0.102511   
5  Herne Hill Road, Herne Hill, London Borough of...  51.459907  -0.094173   
6  Sainsbury's, 80, Dog Kennel Hill, East Dulwich...  51.461006  -0.085835   
7  Mount Pond, Windmill Drive, Abbeville Village,...  51.457261  -0.149889   
8  Lambeth College, 45, Clapham Common South Side...  51.458364  -0.141553   
9  Clapham Park Road, Abbeville Village, Clapham ...  51.459466  -0.133217   

              X             Y  Distance from center  
0 -548812.46846  5.809841e+06           5992.495307  
1 -548212.46846  5.809841e+06           5840.376700  
2 -547612.46846  5.809841e+06           5747.173218  
3 -547012.46846  5.809841e+06           5715.767665  
4 -546412.46846  5.809841e+06           5747.173218  
5 -545812.46846  5.809841e+06           5840.376700  
6 -545212.46846  5.809841e+06           5992.495307  
7 -549712.46846  5.810361e+06           5855.766389  
8 -549112.46846  5.810361e+06           5604.462508  
9 -548512.46846  5.810361e+06           5408.326913

In [12]:
df_locations.to_pickle('./locations.pkl')    

## FourSquare

Here we get the restaurant near each neighbors

In [13]:
food_category = '4d4b7105d754a06374d81259' 
italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

In [14]:

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Greater London', '')
    address = address.replace(', United Kingdom', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [15]:
import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, CLIENT_ID, CLIENT_SECRET, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_italian:
                    italian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, italian_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
italian_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('italian_restaurants_350.pkl', 'rb') as f:
        italian_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, italian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('italian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(italian_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
        

Restaurant data loaded.


In [16]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 2957
Total number of Italian restaurants: 435
Percentage of Italian restaurants: 14.71%
Average number of restaurants in neighborhood: 7.3791208791208796


In [17]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4f36cda5e4b00af1794f9e73', 'Bistro Union', 51.4543814946221, -0.13988732409507973, '40 Abbeville Rd, London, SW4 6NG', 279, False, -549090.6732396316, 5809897.2585512595)
('532456d1498ea72a7dd6da5d', 'Tokyo Retro', 51.45458799311766, -0.13965004754211566, '57 Abbeville Road, London, SW4 9JW', 263, False, -549069.5063997398, 5809916.570855112)
('4e8617229a52a426022d5fb7', 'The Abbeville Kitchen', 51.45432647310704, -0.1399971114767822, '47 Abbeville Rd., London, SW4 0JX', 287, False, -549099.5213740016, 5809892.791754158)
('58f7ab9fa35dce4c76339235', '33 Abbeville Road', 51.454055, -0.1403, 'London, SW4', 310, False, -549126.7253096951, 5809867.271068442)
('5707ad52498ed6d538cc29ec', 'May The Fifteenth', 51.45422, -0.14009479, '47 Abbeville Rd, London, SW4 9JX', 294, False, -549108.7360357493, 5809882.474512659)
('4d3dd4ccfb4c54816592e014', 'Curry Paradise', 51.45505037594604, -0.11942077746729092, 'Brixton Hill (Josephine Ave.), Brixton

In [18]:
print('List of Italian restaurants')
print('---------------------------')
for r in list(italian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(italian_restaurants))

List of Italian restaurants
---------------------------
('4bf8fe195efe2d7fd6986b34', 'La Baita', 51.458227731276466, -0.14880104944307312, 'Clapham Common North Side, Clapham, SW4 0QW', 131, True, -549614.9818675444, 5810451.410157608)
('59a92e91b2958f5516333c88', 'Canova Hall', 51.46393661129359, -0.11513047452350199, '250 Ferndale Rd, London, SW9 8BQ', 322, True, -547162.3360713229, 5810590.321695896)
('5766787c498e84f6e8288f04', 'Franzina Trattoria', 51.463492, -0.112374, 'United Kingdom', 300, True, -546982.8164496595, 5810501.174047431)
('53369f55498ec0b8cac28896', 'Artusi', 51.46672969666967, -0.07284656623155056, '161 Bellenden Rd, London, SE15 4DH', 146, True, -544184.6752071743, 5810283.805052945)
('4bc9a1e3b6c49c7478b28e91', 'Buonasera', 51.460021247686385, -0.16663788243523334, '22-26 Northcote Rd., London, SW11 1NX', 188, True, -550801.8196322026, 5810909.564994309)
('4bd357479854d13a338efd4d', 'Osteria Antica Bologna', 51.45994731873175, -0.16660641909450333, '23 Northcote

In [19]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: Restaurant Gordon Ramsay, Maze Grill, The Sizzling Squid
Restaurants around location 102: M&G Vip Lounge :-)
Restaurants around location 103: Pimlico Spice
Restaurants around location 104: Khallouk & Taylor, Goya, Pimlico Tandoori, Millbank Spice
Restaurants around location 105: Casa Madeira, Waterfront London Vauxhall Restaurant, Rex Whistler, Pico Bar & Grill, STEAX AND THE CITY
Restaurants around location 106: Ragged Canteen
Restaurants around location 107: Samsun Kebab
Restaurants around location 108: Sabor Peruano, Toulouse Lautrec, Dragon Castle, Chatkhara, Leños y Carbón, La Bodeguita Restaurant, After Taste Chinese Rest. 返寻味, Chatica
Restaurants around location 109: Lebanese Grill
Restaurants around location 110: Tower Cafe, Jad Grill, Tower Tandoori, Crystal China 味缘 （伦敦最强麻辣香锅 川菜）, Navarro


Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in different color.

In [20]:
map_London = folium.Map(location=[latitude, longitude], zoom_start=13)
folium.Marker(location=[latitude, longitude], popup='London').add_to(map_London)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_London)
map_London

Now we have all the restuarants in the areas within 6km from London city center. And the Italian restaurants are also labeled (red points) on the map. In addition, we also know the restaurants near each neighbors.
Next, we will make most use of this data to do analysis to seek the optimal option for a new Italian restaurant.

## Methodology 

In this project our aims is to find the lowest density area of restaurants as well as few Italian restaurants.
We limimt 6km around the city center.
In the first stage we get the location and type of all restaurant in around the city center and the similar Italian restaurants.
In the second step, we will focus on the neighborhood areas who are surrounded by less restaurants or no Italian restaurants.
In the last step, we will ues K-means cluster to see whether the clusters meets the basic requirement of the stakeholders.
And we will present all such choice on the map for the selection of stakeholders

**Analysis** 

Count the number of restaurant near the neiborhood area

In [22]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 7.3791208791208796


Address   Latitude  Longitude  \
0  Elms Crescent, Abbeville Village, Clapham Park...  51.454405  -0.135857   
1  Londis, 17-20, Prague Place, Abbeville Village...  51.455507  -0.127522   
2  Trinity Academy, 56, Brixton Hill, Stockwell, ...  51.456608  -0.119185   
3  Jelf Road, Herne Hill, London Borough of Lambe...  51.457708  -0.110849   
4  Milkwood Road, West Dulwich, Herne Hill, Londo...  51.458808  -0.102511   
5  Herne Hill Road, Herne Hill, London Borough of...  51.459907  -0.094173   
6  Sainsbury's, 80, Dog Kennel Hill, East Dulwich...  51.461006  -0.085835   
7  Mount Pond, Windmill Drive, Abbeville Village,...  51.457261  -0.149889   
8  Lambeth College, 45, Clapham Common South Side...  51.458364  -0.141553   
9  Clapham Park Road, Abbeville Village, Clapham ...  51.459466  -0.133217   

              X             Y  Distance from center  Restaurants in area  
0 -548812.46846  5.809841e+06           5992.495307                    4  
1 -548212.46846  5.809841e+06           5840.376700                    0  
2 -547612.46846  5.809841e+06           5747.173218                    2  
3 -547012.46846  5.809841e+06           5715.767665                    0  
4 -546412.46846  5.809841e+06           5747.173218                    0  
5 -545812.46846  5.809841e+06           5840.376700                    0  
6 -545212.46846  5.809841e+06           5992.495307                    0  
7 -549712.46846  5.810361e+06           5855.766389                    1  
8 -549112.46846  5.810361e+06           5604.462508                    1  
9 -548512.46846  5.810361e+06           5408.326913                    4

calculate the distance to nearest Italian restaurant from every area candidate center

In [23]:
distances_to_italian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in italian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_italian_restaurant.append(min_distance)

df_locations['Distance to Italian restaurant'] = distances_to_italian_restaurant

In [24]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  Elms Crescent, Abbeville Village, Clapham Park...  51.454405  -0.135857   
1  Londis, 17-20, Prague Place, Abbeville Village...  51.455507  -0.127522   
2  Trinity Academy, 56, Brixton Hill, Stockwell, ...  51.456608  -0.119185   
3  Jelf Road, Herne Hill, London Borough of Lambe...  51.457708  -0.110849   
4  Milkwood Road, West Dulwich, Herne Hill, Londo...  51.458808  -0.102511   
5  Herne Hill Road, Herne Hill, London Borough of...  51.459907  -0.094173   
6  Sainsbury's, 80, Dog Kennel Hill, East Dulwich...  51.461006  -0.085835   
7  Mount Pond, Windmill Drive, Abbeville Village,...  51.457261  -0.149889   
8  Lambeth College, 45, Clapham Common South Side...  51.458364  -0.141553   
9  Clapham Park Road, Abbeville Village, Clapham ...  51.459466  -0.133217   

              X             Y  Distance from center  Restaurants in area  \
0 -548812.46846  5.809841e+06           5992.495307                    4   
1 -548212.46846  5.809841e+06           5840.376700                    0   
2 -547612.46846  5.809841e+06           5747.173218                    2   
3 -547012.46846  5.809841e+06           5715.767665                    0   
4 -546412.46846  5.809841e+06           5747.173218                    0   
5 -545812.46846  5.809841e+06           5840.376700                    0   
6 -545212.46846  5.809841e+06           5992.495307                    0   
7 -549712.46846  5.810361e+06           5855.766389                    1   
8 -549112.46846  5.810361e+06           5604.462508                    1   
9 -548512.46846  5.810361e+06           5408.326913                    4   

   Distance to Italian restaurant  
0                      906.325284  
1                      988.914701  
2                      874.036391  
3                      660.731260  
4                      872.343617  
5                     1343.652103  
6                     1119.079634  
7                      133.145280  
8                      510.630742  
9                      405.267452

In [25]:
print('Average distance to closest Italian restaurant from each area center:', df_locations['Distance to Italian restaurant'].mean())

Average distance to closest Italian restaurant from each area center: 408.30699838343116


In [26]:
import requests
London_boroughs_url = 'https://raw.githubusercontent.com/gitbush/london-boroughs/master/static/data/boroughsGeo.json'
London_boroughs = requests.get(London_boroughs_url).json()

def London_style(feature):
    return { 'color': 'blue', 'fill': False }

In [27]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

a map showing **heatmap / density of restaurants**

In [28]:
from folium import plugins
from folium.plugins import HeatMap

map_London = folium.Map(location=[latitude,longitude], zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_London) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_London)
folium.Marker(location=[latitude,longitude]).add_to(map_London)
folium.Circle(location=[latitude,longitude], radius=1000, fill=False, color='white').add_to(map_London)
folium.Circle(location=[latitude,longitude], radius=2000, fill=False, color='white').add_to(map_London)
folium.Circle(location=[latitude,longitude], radius=3000, fill=False, color='white').add_to(map_London)
folium.GeoJson(London_boroughs, style_function=London_style, name='geojson').add_to(map_London)
map_London

 another heatmap map showing **heatmap/density of Italian restaurants** only.

In [29]:
map_London = folium.Map(location=[latitude,longitude], zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_London) #cartodbpositron cartodbdark_matter
HeatMap(italian_latlons).add_to(map_London)
folium.Marker(location=[latitude,longitude]).add_to(map_London)
folium.Circle(location=[latitude,longitude], radius=1000, fill=False, color='white').add_to(map_London)
folium.Circle(location=[latitude,longitude], radius=2000, fill=False, color='white').add_to(map_London)
folium.Circle(location=[latitude,longitude], radius=3000, fill=False, color='white').add_to(map_London)
folium.GeoJson(London_boroughs, style_function=London_style, name='geojson').add_to(map_London)
map_London

From above heatmap, we can easily get that the north and south east area has the least restaurants  and Italian restaurants

**Pimlico and Kennington**

Pimlico:
''Pimlico  is an area of Central London in the City of Westminster, built as a southern extension to neighbouring Belgravia.[1] It is known for its garden squares and Regency architecture. It is demarcated to the north by Victoria Station, and bounded by the River Thames to the south, Vauxhall Bridge Road to the east and the former Grosvenor Canal to the west. At its heart is a grid of residential streets laid down by the planner Thomas Cubitt, beginning in 1825 and now protected as the Pimlico Conservation Area. Additions have included the pre-World War II Dolphin Square and the Churchill Gardens and Lillington and Longmoore Gardens estates, now conservation areas in their own right. The area has over 350 Grade II listed buildings and several Grade II* listed churches.''(From Wikipedia)
Kennington:
''Kennington is the location of three significant London landmarks: the Oval cricket ground, the Imperial War Museum, and Kennington Park. Its population at the United Kingdom Census 2011 was 15,106. Kennington is served by Kennington Police Station.''(From Wikipedia)
Large population, Popular with tourists,near the city center,these borough appear to justify further analysis.
Next we will focus on these two borough.

In [33]:
roi_x_min = London_center_x - 2000
roi_y_max = London_center_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_London = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_London)
folium.Marker([latitude,longitude]).add_to(map_London)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_London)
folium.GeoJson(London_boroughs, style_function=London_style, name='geojson').add_to(map_London)
map_London

C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Not bad. It shows the lowest density of restaurants area in Lambeth and Southwark
Then we create new, more dense grid of location candidates restricted to our new region of interest

In [34]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyp

2261 candidate neighborhood centers generated.


C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Italian restaurant**.

In [37]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_italian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, italian_restaurants)
    roi_italian_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [38]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Italian restaurant':roi_italian_distances})

df_roi_locations.head(10)

Latitude  Longitude             X             Y  Restaurants nearby  \
0  51.473427  -0.109631 -546562.46846  5.811557e+06                   0   
1  51.473610  -0.108241 -546462.46846  5.811557e+06                   0   
2  51.473170  -0.117531 -547112.46846  5.811643e+06                   1   
3  51.473353  -0.116141 -547012.46846  5.811643e+06                   0   
4  51.473537  -0.114751 -546912.46846  5.811643e+06                   1   
5  51.473720  -0.113361 -546812.46846  5.811643e+06                   1   
6  51.473904  -0.111971 -546712.46846  5.811643e+06                   1   
7  51.474087  -0.110581 -546612.46846  5.811643e+06                   0   
8  51.474270  -0.109191 -546512.46846  5.811643e+06                   0   
9  51.474454  -0.107801 -546412.46846  5.811643e+06                   0   

   Distance to Italian restaurant  
0                     1136.309530  
1                     1176.974488  
2                     1054.336957  
3                     1063.766864  
4                     1082.392472  
5                     1109.750867  
6                     1145.216359  
7                     1188.063142  
8                     1235.348984  
9                     1276.775905

we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Italian restaurants in radius of 400 meters**.

In [39]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to Italian restaurant']>=400)
print('Locations with no Italian restaurants within 400m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 931
Locations with no Italian restaurants within 400m: 771
Locations with both conditions met: 564


In [42]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_London = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_London)
HeatMap(restaurant_latlons).add_to(map_London)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_London)
folium.Marker([latitude,longitude]).add_to(map_London)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_London) 
folium.GeoJson(London_boroughs, style_function=London_style, name='geojson').add_to(map_London)
map_London

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Italian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [45]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_London = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_London)
HeatMap(restaurant_latlons).add_to(map_London)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_London)
folium.Marker([latitude,longitude]).add_to(map_London)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_London) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_London)
folium.GeoJson(London_boroughs, style_function=London_style, name='geojson').add_to(map_London)
map_London

C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyp

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [46]:
map_London = folium.Map(location=roi_center, zoom_start=14)
folium.Marker([latitude,longitude]).add_to(map_London)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_London)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_London)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_London) 
folium.GeoJson(London_boroughs, style_function=London_style, name='geojson').add_to(map_London)
map_London

candidate areas in **Pimlico**:

In [51]:
map_London = folium.Map(location=[51.489, -0.137], zoom_start=15)
folium.Marker([latitude,longitude]).add_to(map_London)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_London) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_London)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_London)
folium.GeoJson(London_boroughs, style_function=London_style, name='geojson').add_to(map_London)
map_London

candidate areas in **Kennington**:

In [53]:
map_London = folium.Map(location=[51.4838,-0.1053], zoom_start=15)
folium.Marker([latitude,longitude]).add_to(map_London)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_London) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_London)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_London)
folium.GeoJson(London_boroughs, style_function=London_style, name='geojson').add_to(map_London)
map_London

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [55]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(lat, lon).replace(',United Kingdom', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, London_center_x, London_center_y)
    print('{}{} => {:.1f}km from London'.format(addr, ' '*(50-len(addr)), d/1000))

Addresses of centers of areas recommended for further analysis



C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


ARK All Saints Academy, 140, Wyndham Road, Wyndham and Comber Estate, Camberwell, London Borough of Southwark, London, Greater London, England, SE5 0UB, United Kingdom => 3.7km from London


C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


Blackstone House, Glasgow Terrace, Pimlico, City of Westminster, London, Greater London, England, SW1V 3AB, United Kingdom => 2.5km from London


...

C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


Brixton Road, Kennington, London Borough of Lambeth, London, Greater London, England, SE11 5TP, United Kingdom => 3.1km from London


C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


Lorrimore Square, Borough, Elephant and Castle, London Borough of Southwark, London, Greater London, England, SE17 3QU, United Kingdom => 3.1km from London
Christ Church Primary, Cancell Road, Kennington, London Borough of Lambeth, London, Greater London, England, SW9 6HN, United Kingdom => 3.8km from London


C:\Users\13652\anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


Here is the end of our analysis. It concludes 15 addresses which has lower number of restaurant and no Italian restaurant nearby. All this zones are near the city center(less than 4km). All the zones are showing on map with 500m radius. Most of these zones are located at Kennington and Pimlico which is identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport. 

## 3.Result and  Discussion

Our analysis shows that although there is a great number of restaurants in London, there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected middle and west from London, so we focused our attention to areas south, south-east and east, corresponding to Pimlico and Kennington.Our attention was focused on Pimlico and Kennington which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics and a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Italian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to London center but not crowded with existing restaurants (particularly Italian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## 4.Conclusion

Purpose of this project was to identify London areas close to center with low number of restaurants (particularly Italian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Italian restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.